# Beach profile classifier
Using RANSAC algorithm

## Setup notebook

In [ ]:
# Enable autoreloading of our modules. 
# Most of the code will be located in the /src/ folder, 
# and then called from the notebook.
%matplotlib inline
%reload_ext autoreload
%autoreload

In [ ]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os
import decimal
import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
from plotly import tools
import plotly.io as pio
from scipy import stats
import math
import matplotlib
from matplotlib import cm
import colorlover as cl
import numpy.ma as ma

from ipywidgets import widgets, Output
from IPython.display import display, clear_output, Image, HTML

from sklearn.metrics import confusion_matrix

import numpy as np
from matplotlib import pyplot as plt

from sklearn import linear_model, datasets

In [ ]:
# Matplot lib default settings
plt.rcParams["figure.figsize"] = (10,3)
plt.rcParams['axes.grid']=True
plt.rcParams['grid.alpha'] = 0.5
plt.rcParams['grid.color'] = "grey"
plt.rcParams['grid.linestyle'] = "--"

## Import data

In [ ]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_waves = df_from_csv('waves.csv', index_col=[0, 1])
df_tides = df_from_csv('tides.csv', index_col=[0, 1])
df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_sites = df_from_csv('sites.csv', index_col=[0])
df_profile_features_crest_toes = df_from_csv('profile_features_crest_toes.csv', index_col=[0,1])

# Note that the forecasted data sets should be in the same order for impacts and twls
impacts = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('impacts_forecasted_foreshore_slope_sto06.csv', index_col=[0]),
        'mean_slope_sto06': df_from_csv('impacts_forecasted_mean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }


twls = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('twl_foreshore_slope_sto06.csv', index_col=[0, 1]),
        'mean_slope_sto06':df_from_csv('twl_mean_slope_sto06.csv', index_col=[0, 1]),
    }
}
print('Done!')

# Implement algorithm

## Get profile data

In [ ]:
def get_profile_data(site, profile_type, df_profiles):
    """
    Returns a list of x and z coordinates for a given profile.
    """

    # Get x and z coorindates of profile
    x = df_profiles.loc[(site, profile_type)].index.values
    z = df_profiles.loc[(site, profile_type)].z.values

    # Get land limit
    land_lim = df_profiles.loc[(site, 'poststorm')].land_lim.loc[0]

    # Remove nan values
    m = ma.masked_invalid(z)
    x = x[~m.mask]
    z = z[~m.mask]

#     # Remove landwards of landlim
#     mask = ma.masked_where(x < land_lim, x)
#     x = x[~mask.mask]
#     z = z[~mask.mask]

    return x, z


# Load profile data
# site = 'WAMBE0010'
# site = 'NINEMs0048'
# site = 'NAMB0013'
# site = 'AVOCAn0009'
# site = 'GRANTSs0014'
site = 'NARRA0001'
profile_type = 'prestorm'
x, z = get_profile_data(site, profile_type, df_profiles)

print('x = {} ...'.format(x[0:5]))
print('z = {} ...'.format(z[0:5]))

In [ ]:



# # n_samples = 1000
# # n_outliers = 50


# # X, y, coef = datasets.make_regression(n_samples=n_samples, n_features=1,
# #                                       n_informative=1, noise=10,
# #                                       coef=True, random_state=0)

# # # Add outlier data
# # np.random.seed(0)
# # X[:n_outliers] = 3 + 0.5 * np.random.normal(size=(n_outliers, 1))
# # y[:n_outliers] = -3 + 10 * np.random.normal(size=n_outliers)

# # # Fit line using all data
# # lr = linear_model.LinearRegression()
# # lr.fit(X, y)

# # Robustly fit linear model with RANSAC algorithm
# ransac = linear_model.RANSACRegressor()
# ransac.fit(x, z)
# inlier_mask = ransac.inlier_mask_
# outlier_mask = np.logical_not(inlier_mask)

# # Predict data of estimated models
# line_x = np.arange(x.min(), x.max())[:, np.newaxis]
# line_y_ransac = ransac.predict(line_x)

# lw = 2
# plt.scatter(x[inlier_mask], z[inlier_mask], color='yellowgreen', marker='.',
#             label='Inliers')
# plt.scatter(x[outlier_mask], z[outlier_mask], color='gold', marker='.',
#             label='Outliers')
# plt.plot(line_x, line_y_ransac, color='cornflowerblue', linewidth=lw,
#          label='RANSAC regressor')
# plt.legend(loc='lower right')
# plt.xlabel("Input")
# plt.ylabel("Response")
# plt.show()

## Fit linear interpolated spline to profile
- Linear interpolated spline used to simplify the profile.
- Need to do a bit of optimization to calculate the best smoothing parameter for the profile.

In [ ]:
from scipy.interpolate import UnivariateSpline
from scipy.interpolate import interp1d


def pairwise(iterable):
    "s -> (s0,s1), (s1,s2), (s2, s3), ..."
    a, b = itertools.tee(iterable)
    next(b, None)
    return zip(a, b)


def xz(x_start, x_end, x, z):
    """
    Returns a list of x coordinates and z coorindates which lie between x_start and x_end
    """
    x_seg = [val for val in x if x_start <= val <= x_end]
    z_seg = [z_val for x_val, z_val in zip(x, z) if x_start <= x_val <= x_end]
    return x_seg, z_seg


def get_slope(x, z):
    slope, intercept, r_value, p_value, std_err = linregress(x, z)
    return slope


def get_r_squared(x, z):
    slope, intercept, r_value, p_value, std_err = linregress(x, z)
    return r_value**2


def rolling_std(a, w):
    """
    Calculates a rolling window standard deviation
    https://stackoverflow.com/a/40773366
    """
    a = np.array(a)
    nrows = a.size - w + 1
    n = a.strides[0]
    a2D = np.lib.stride_tricks.as_strided(a, shape=(nrows, w), strides=(n, n))
    return np.std(a2D, 1)


def iterate_over_smoothing_params(x, z):
    """
    Finds the best smoothing parameter for a linear interpolated spline. 
    Checks a number of smoothing factors, and then tries to minimize the 
    number of knots (changepoints) while retaining decent match to the 
    original profile.
    """

    # Store the results of our iterations in a list of dictionaries
    results = []

    # Iterate through different value of smoothing parameters
    s_vals = [x for x in np.arange(0, 10, 0.01)]

    r2_vals = []
    n_knots = []
    s_vals_to_keep = []

    # Iterate backwards just to make further calcultions more easier.
    for s_val in s_vals[::-1]:

        # Fit spline to profile using the s_val for this iteration
        # k=1 is used to force linear line segments between knots
        s = UnivariateSpline(x, z, s=s_val, k=1)
        xs = np.linspace(x[0], x[-1], 1000)
        zs = s(xs)

        # Find knots
        x_knots = s.get_knots()
        z_knots = s(x_knots)

        # Get number of knots
        n = len(s.get_knots())

        # If we've already recorded data about this number of knots, just skip.
        # Need to also, only have increasing results for spline interpolation
        if n in [x['n'] for x in results
                 ] or n < max([x['n'] for x in results], default=0):
            continue

        # Get r2, how well does the simplification fit the original profile?
        # Create interp model from the knots at our original points.
        f = interp1d(x_knots, z_knots)
        z_lin = f(x)
        r2 = get_r_squared(z, z_lin)

        results.append({'n': n, 's': s_val, 'r2': r2})
    return results


def find_best_smoothing_param(results, min_std=0.0002):
    """
    Given a list of smoothing parameters and their fits, determine what the best smoothing parameter is.
    Larger min_std = more smoothing
    """

    # Get the 2nd derivate of the n_knots vs r2_vals.
    y_spl = UnivariateSpline([x['n'] for x in results],
                             [x['r2'] for x in results],
                             s=0)
    y_spl_2d = y_spl.derivative(n=2)
    y_spl_2d_vals = y_spl_2d([x['n'] for x in results])

    # Get a rolling standard deviation of the derivative
    std = rolling_std(y_spl_2d_vals, w=3)

    # Best smoothing parameter will be when the standard deviation stops changing
    best_i = np.argmax(std < min_std)
    best_s = results[best_i]['s']
    return best_s


def simplify_profile(x, z, site):
    results = iterate_over_smoothing_params(x, z)
    best_s = find_best_smoothing_param(results)

    # Fit spline to profile
    s = UnivariateSpline(x, z, s=best_s, k=1)
    xs = np.linspace(x[0], x[-1], 1000)
    zs = s(xs)

    # Find knots
    x_knots = s.get_knots()
    z_knots = s(x_knots)

    # Plot for checking
    plt.title('{}: Linear spline simplification'.format(site))
    plt.xlabel('Distance (m)')
    plt.ylabel('Elevation (m AHD)')
    plt.plot(x, z, 'k.-', label='Raw profile')
    plt.plot(
        xs, zs, 'r-', label='Interpolated profile (s={:.2f})'.format(best_s))
    plt.plot(
        x_knots,
        z_knots,
        'ro',
        markersize=8,
        markeredgewidth=1.5,
        markeredgecolor='orange',
        label='Interpolated knots (n={})'.format(len(x_knots)))
    plt.legend(loc='best')
#     plt.show()

    return x_knots, z_knots, best_s


x_knots, z_knots, best_s = simplify_profile(x, z, site)

In [ ]:
def get_x_z_from_knots(x_knots, z_knots):
    # Fit spline to profile
    s = UnivariateSpline(x_knots, z_knots, s=0, k=1)
    xs = np.linspace(x_knots[0], x_knots[-1], 1000)
    zs = s(xs)
    return xs, zs

def simplify_segments_with_same_slopes(x_knots, x, z, site, best_s):
    """
    Removes knots which have similar slopes on either side. 
    This is an extra simplifcation as the linear splines may still include
    some nodes that aren't required.
    """
    removed_x_knots = []
    while True:
        for x_knot1, x_knot2, x_knot3 in zip(x_knots[0:-2], x_knots[1:-1], x_knots[2:]):

            # Get slope of segment behind point at x_knot2
            x_seg, z_seg = xz(x_knot1, x_knot2, x, z)
            slope1 = get_slope(x_seg, z_seg)

            # Get slope of line in front of point at x_knot2
            x_seg, z_seg = xz(x_knot2, x_knot3, x, z)
            slope2 = get_slope(x_seg, z_seg)

            slope_diff = abs(slope1 - slope2)

            # Also check if points are too close together
            if x_knot3 - x_knot1 < 3: # m
                too_close = True
            else:
                too_close = False
            
            # Good, the slopes are different on each side, keep checking
            if slope_diff > 0.01 and too_close == False:
                continue
            # Else bad, slopes are the same so we have to remove this point
            else:
                print('Knot at x={} removed (slope_diff={:.3f})'.format(
                    x_knot2, slope_diff))
                x_knots = np.delete(x_knots, np.where(x_knots == x_knot2), axis=0)
                removed_x_knots.append(x_knot2)
                break

        else:
            print("All segments have different slopes")
            x_knots_simplified = x_knots
            z_knots_simplified = [
                z_val for x_val, z_val in zip(x, z) if x_val in x_knots_simplified
            ]
            break
    
    # Find z location of our removed knots
    removed_z_knots = [
                z_val for x_val, z_val in zip(x, z) if x_val in removed_x_knots
            ]
    
    # Get the new interpolated spline from our simplified knots
    xs, zs = get_x_z_from_knots(x_knots_simplified, z_knots_simplified)
    
    # Plot for checking
#     plt.title('{}: Linear spline simplification by comparing slopes'.format(site))
#     plt.xlabel('Distance (m)')
#     plt.ylabel('Elevation (m AHD)')
#     plt.plot(x, z, 'k.-', label='Raw profile')
#     plt.plot(
#         xs, zs, 'r-', label='Interpolated profile (s={:.2f})'.format(best_s))
#     plt.plot(
#         x_knots_simplified,
#         z_knots_simplified,
#         'ro',
#         markersize=8,
#         markeredgewidth=1.5,
#         markeredgecolor='orange',
#         label='Interpolated knots (n={})'.format(len(x_knots)))
#     plt.plot(
#         removed_x_knots,
#         removed_z_knots,
#         'ro',
#         markersize=10,
#         markeredgewidth=2.5,
#         markerfacecolor="None",
#         markeredgecolor='orange',
#         label='Removed knots (n={})'.format(len(removed_x_knots)))
#     plt.legend(loc='best')
#     plt.show()

    return x_knots_simplified,z_knots_simplified

x_knots, z_knots = simplify_segments_with_same_slopes(x_knots, x, z, site, best_s)
xs, zs = get_x_z_from_knots(x_knots, z_knots)

In [ ]:
## BACKUP
def find_crest_and_toes(x,z,x_knots,best_s):

    # Get a cubic spline so we can have continuous second order deriviates for our profile
#     spl = interpolate.splrep(x, z, k=4,t=x_knots[1:-1])
    spl = interpolate.splrep(x, z, k=3,s=best_s)

    xx = np.linspace(x[0], x[-1], 1000)
    zz = interpolate.splev(xx, spl)
    zz_d1 = interpolate.splev(xx, spl, der=1)
    zz_d2 = interpolate.splev(xx, spl, der=2)
    zz_d3 = interpolate.splev(xx, spl, der=3)

    try:
        # Find dune crest by looking at elevation
        peaks_crest, props_crest = find_peaks(zz, height=3, prominence=0.5)
        
        # Save potential crests
        x_potential_crests = xx[peaks_crest]
        z_potential_crests = zz[peaks_crest]

        # Take most seaward peak as dune crest
        i_crest = peaks_crest[-1]
        x_crest = xx[i_crest]
        z_crest = zz[i_crest]

        print('Found {} potential dune crests from elevation'.format(len(peaks_crest)))

    except:
        print('No crests found from elevation')
        x_crest = np.nan
        z_crest = np.nan
        pass

    try:
        if np.isnan(x_crest) and np.isnan(x_crest):
            # Find dune crest by looking at 2nd deriviate
            # Multiply by -1 since crest will have a negative 2nd derivative and we want to find peaks (i.e. positive)
            peaks_crest, props_crest = find_peaks(zz_d2*-1, height=0.02,width=0)
            
            
            # Save potential crests
            x_potential_crests = xx[peaks_crest]
            z_potential_crests = zz[peaks_crest]
            print('Found {} potential dune crests from 2nd derivitive'.format(len(peaks_crest)))

            # Take peak with biggest height
            i_biggest_crest = np.argmax(props_crest['peak_heights'])
            i_crest = peaks_crest[i_biggest_crest]
#             x_crest = xx[i_crest]
#             z_crest = zz[i_crest]

            # Then take the left base of that peak
            x_crest = xx[props_crest['left_bases'][i_biggest_crest]]
            z_crest= zz[props_crest['left_bases'][i_biggest_crest]]


    except:
        # Take crest as location with maximum elevation
        i_crest = np.argmax(zz)
        x_crest = xx[i_crest]
        z_crest = zz[i_crest]
        print('No crest found, taking maximum elevation as crest')

    try:
        # Find due toe
        peaks_toe, props_toe = find_peaks(zz_d2, height=0, prominence=0.02)
#         peaks_toe, props_toe = find_peaks(zz_d2, height=-3, prominence=0.00)

        # Save potential crests
        x_potential_toes = xx[peaks_toe]
        z_potential_toes = zz[peaks_toe]

        # Remove toes which are behind dune crest
        heights_toe = props_toe['peak_heights'][peaks_toe > i_crest]
        peaks_toe = peaks_toe[peaks_toe > i_crest]

        # Remove toes that are less than 0.5m in height from dune crest

        mask = z_crest-0.5>zz[peaks_toe]
        heights_toe = heights_toe[mask]
        peaks_toe = peaks_toe[mask]

        # Take toe with biggest 2nd derivative height
        i_toe = peaks_toe[np.argmax(heights_toe)]
        x_toe = xx[i_toe]
        z_toe = zz[i_toe]
        print('Found {} potential dune toes from 2nd derivitive'.format(len(peaks_toe)))

#         # The above method usually results in a toe value which is slightly too high up.
#         # We can improve this by moving the toe seaward to the next negative peak in the third
#         # derivative of elevation
#         peaks_toe_d3, props_toe_d3 = find_peaks(zz_d3*-1, height=0.03, prominence=0.02)

#         # Filter everything landward of the previous toe position, then take the first (most landward) peak
#         mask = xx[peaks_toe_d3] > x_toe
#         peaks_toe_d3 = peaks_toe_d3[mask]

#         if peaks_toe_d3.size != 0:
#             print('Adjusting toe position based on d3')
#             x_toe = xx[peaks_toe_d3[0]]
#             z_toe = zz[peaks_toe_d3[0]]

#         # Move toe forward to based on the third derivative of elevation
#         print('Adjusting toe position based on d3')
#         mask = (zz_d3 > -0.0008) & (xx > x_toe) & (np.r_[np.diff(zz_d3)[0],np.diff(zz_d3)] > 0)
#         x_toe = xx[mask][1]
#         z_toe = zz[mask][1]

    except:
        x_toe = np.nan
        z_toe = np.nan
        print('No toe found')
    
    return xx,zz, zz_d1,zz_d2,zz_d3,x_crest,z_crest, x_toe,z_toe, x_potential_crests,z_potential_crests, x_potential_toes,z_potential_toes

In [ ]:
def find_crest_and_toes(x,z,x_knots,best_s):

    # Get a cubic spline so we can have continuous second order deriviates for our profile
#     spl = interpolate.splrep(x, z, k=4,t=x_knots[1:-1])
    spl = interpolate.splrep(x, z, k=3,s=best_s)

    xx = np.linspace(x[0], x[-1], 1000)
    zz = interpolate.splev(xx, spl)
    zz_d1 = interpolate.splev(xx, spl, der=1)
    zz_d2 = interpolate.splev(xx, spl, der=2)
    zz_d3 = interpolate.splev(xx, spl, der=3)

    # Find the biggest slopes
    peaks, props = find_peaks(zz_d1*-1, height=0.15, width=0,prominence=0.1)

    if len(peaks) != 0:

        x_potential_crests =[xx[val] for val in props['left_bases']]
        x_potential_toes =[xx[val] for val in props['right_bases']]
        x_potential_heights = [val for val in props['peak_heights']]
        x_potential_face_center = xx[peaks]

        # Put a limit on how when a slope ends.
        # Dune faces has to be steeper than this value
#         min_slope = -0.10

        x_new_potential_crests = []
        x_new_potential_toes = []
        z_new_potential_crests = []
        z_new_potential_toes = []
        dune_heights = []
        slopes = []

        for x_crest, x_center, x_toe,height in zip(x_potential_crests, x_potential_face_center, x_potential_toes,x_potential_heights):
            print('Checking x_crest={:.2f}m,x_center={:.2f}m,x_toe={:.2f}m'.format(x_crest, x_center, x_toe))

            min_slope = height/-6
            # Check the land side of the dune face
            land_mask = ((x_crest<=xx)&(xx<=x_center))
            land_slope_okay = zz_d1[land_mask]<min_slope
            x_land_slope_okay = xx[land_mask][~land_slope_okay]
            if len(x_land_slope_okay) == 0:
                x_new_crest = x_crest
            else:
                x_new_crest = x_land_slope_okay[-1]
            idx_new_crest = np.where(x_new_crest==xx)[0]
            z_new_crest = zz[idx_new_crest][0]

    #         # TODO Check, for now, keep crest as detected level
    #         # Maybe we don't need to change
    #         x_new_crest = x_crest
    #         idx_new_crest = np.where(x_new_crest==xx)[0]
    #         z_new_crest = zz[idx_new_crest][0]
    #         ###

            # Check the sea side of the dune face
            sea_mask = ((x_center<=xx)&(xx<=x_toe))
            sea_slope_okay = zz_d1[sea_mask]<min_slope
            x_sea_slope_okay = xx[sea_mask][~sea_slope_okay]
            if len(x_sea_slope_okay) == 0:
                x_new_toe = x_toe
            else:
                x_new_toe = x_sea_slope_okay[0]
            idx_new_toe = np.where(x_new_toe==xx)[0]
            z_new_toe = zz[idx_new_toe][0]

            slopes.append((z_new_crest - z_new_toe)/(x_new_crest - x_new_toe))
            dune_heights.append(z_new_crest - z_new_toe)
            x_new_potential_crests.append(x_new_crest)
            x_new_potential_toes.append(x_new_toe)
            z_new_potential_crests.append(z_new_crest)
            z_new_potential_toes.append(z_new_toe)

        # Specifiy minimum dune crest elevation and minimum dune height
        min_dune_ele = np.median(zz)/3 # m AHD
        print('min_dune_ele: {:.2f}m'.format(min_dune_ele))
        min_dune_height = 0.5 # m
        mask = (np.array(z_new_potential_crests) > min_dune_ele) & (np.array(dune_heights) > min_dune_height )

        slopes = np.array(slopes)[mask]
        dune_heights = np.array(dune_heights)[mask]    
        x_potential_crests = np.array(x_new_potential_crests)[mask]
        x_potential_toes = np.array(x_new_potential_toes)[mask]
        z_potential_crests = np.array(z_new_potential_crests)[mask]
        z_potential_toes = np.array(z_new_potential_toes)[mask]

#         # Select dune by largest dune height
#         i_dune = np.argmax(dune_heights)

        ## TODO Throws error if x_potential_crests is empty

        # Select dune by most seaward
        i_dune = np.argmax(x_potential_crests)


        
#         # Select dune by biggest slope
#         i_dune =np.argmax(slopes*-1)
        x_crest = x_potential_crests[i_dune]
        x_toe = x_potential_toes[i_dune]
        z_crest = z_potential_crests[i_dune]
        z_toe = z_potential_toes[i_dune]

    #     try:
    #         # Find dune crest by looking at elevation
    #         peaks_crest, props_crest = find_peaks(zz, height=3, prominence=0.5)

    #         # Save potential crests
    #         x_potential_crests = xx[peaks_crest]
    #         z_potential_crests = zz[peaks_crest]

    #         # Take most seaward peak as dune crest
    #         i_crest = peaks_crest[-1]
    #         x_crest = xx[i_crest]
    #         z_crest = zz[i_crest]

    #         print('Found {} potential dune crests from elevation'.format(len(peaks_crest)))

    #     except:
    #         print('No crests found from elevation')
    #         x_crest = np.nan
    #         z_crest = np.nan
    #         pass

    #     try:
    #         if np.isnan(x_crest) and np.isnan(x_crest):
    #             # Find dune crest by looking at 2nd deriviate
    #             # Multiply by -1 since crest will have a negative 2nd derivative and we want to find peaks (i.e. positive)
    #             peaks_crest, props_crest = find_peaks(zz_d2*-1, height=0.02,width=0)


    #             # Save potential crests
    #             x_potential_crests = xx[peaks_crest]
    #             z_potential_crests = zz[peaks_crest]
    #             print('Found {} potential dune crests from 2nd derivitive'.format(len(peaks_crest)))

    #             # Take peak with biggest height
    #             i_biggest_crest = np.argmax(props_crest['peak_heights'])
    #             i_crest = peaks_crest[i_biggest_crest]
    # #             x_crest = xx[i_crest]
    # #             z_crest = zz[i_crest]

    #             # Then take the left base of that peak
    #             x_crest = xx[props_crest['left_bases'][i_biggest_crest]]
    #             z_crest= zz[props_crest['left_bases'][i_biggest_crest]]


    #     except:
    #         # Take crest as location with maximum elevation
    #         i_crest = np.argmax(zz)
    #         x_crest = xx[i_crest]
    #         z_crest = zz[i_crest]
    #         print('No crest found, taking maximum elevation as crest')

    #     try:
    #         # Find due toe
    #         peaks_toe, props_toe = find_peaks(zz_d2, height=0, prominence=0.02)
    # #         peaks_toe, props_toe = find_peaks(zz_d2, height=-3, prominence=0.00)

    #         # Save potential crests
    #         x_potential_toes = xx[peaks_toe]
    #         z_potential_toes = zz[peaks_toe]

    #         # Remove toes which are behind dune crest
    #         heights_toe = props_toe['peak_heights'][peaks_toe > i_crest]
    #         peaks_toe = peaks_toe[peaks_toe > i_crest]

    #         # Remove toes that are less than 0.5m in height from dune crest

    #         mask = z_crest-0.5>zz[peaks_toe]
    #         heights_toe = heights_toe[mask]
    #         peaks_toe = peaks_toe[mask]

    #         # Take toe with biggest 2nd derivative height
    #         i_toe = peaks_toe[np.argmax(heights_toe)]
    #         x_toe = xx[i_toe]
    #         z_toe = zz[i_toe]
    #         print('Found {} potential dune toes from 2nd derivitive'.format(len(peaks_toe)))

    # #         # The above method usually results in a toe value which is slightly too high up.
    # #         # We can improve this by moving the toe seaward to the next negative peak in the third
    # #         # derivative of elevation
    # #         peaks_toe_d3, props_toe_d3 = find_peaks(zz_d3*-1, height=0.03, prominence=0.02)

    # #         # Filter everything landward of the previous toe position, then take the first (most landward) peak
    # #         mask = xx[peaks_toe_d3] > x_toe
    # #         peaks_toe_d3 = peaks_toe_d3[mask]

    # #         if peaks_toe_d3.size != 0:
    # #             print('Adjusting toe position based on d3')
    # #             x_toe = xx[peaks_toe_d3[0]]
    # #             z_toe = zz[peaks_toe_d3[0]]

    # #         # Move toe forward to based on the third derivative of elevation
    # #         print('Adjusting toe position based on d3')
    # #         mask = (zz_d3 > -0.0008) & (xx > x_toe) & (np.r_[np.diff(zz_d3)[0],np.diff(zz_d3)] > 0)
    # #         x_toe = xx[mask][1]
    # #         z_toe = zz[mask][1]

    #     except:
    #         x_toe = np.nan
    #         z_toe = np.nan
    #         print('No toe found')

    
    else:
        # Take crest as location with maximum elevation
        i_crest = np.argmax(zz)
        x_crest = xx[i_crest]
        z_crest = zz[i_crest]
        x_potential_crests = np.nan
        z_potential_crests = np.nan
        print('No crest found, taking maximum elevation as crest')
        
        x_toe = np.nan
        z_toe = np.nan
        x_potential_toes=np.nan
        z_potential_toes=np.nan
        
    # Check if toe is necessary. If slope of the dune face is similar to the median slope seaward of the dune
    # toe, let's remove the dune toe
    try:
        if np.isnan(x_toe) == False:
            dune_slope =(z_crest - z_toe) / (x_crest - x_toe)
            median_foreshore_slope = np.median(zz_d1[xx > x_toe])
            std_foreshore_slope = np.std(zz_d1[xx>x_toe])
            print('foreshore_std:{:.4f}'.format(std_foreshore_slope))
            print('foreshore_med_slope:{:.4f}'.format(median_foreshore_slope))
            print('dune_slope:{:.4f}'.format(dune_slope))
            if abs(dune_slope - median_foreshore_slope) < 0.075 and std_foreshore_slope <0.025:
                x_toe = np.nan
                z_toe = np.nan
    except:
        pass
        
    return xx,zz, zz_d1,zz_d2,zz_d3,x_crest,z_crest, x_toe,z_toe, x_potential_crests,z_potential_crests, x_potential_toes,z_potential_toes 
        
        
def plot_profile(site, x,z,  xx,zz, zz_d1,zz_d2,zz_d3,x_crest,z_crest, x_toe,z_toe, x_potential_crests,z_potential_crests, x_potential_toes,z_potential_toes):
    plt.figure(figsize=(10,12))
    plt.subplot(411)
    plt.plot(x, z, label='raw')
    plt.plot(xx,zz,label='interpolated')
    plt.plot(x_potential_crests,z_potential_crests,'rv',markersize=10,fillstyle='none',label='Dune crest (potential)')
    plt.plot(x_potential_toes,z_potential_toes,'r^',markersize=10,fillstyle='none',label='Dune toe (potential)')
    plt.plot(x_crest,z_crest,'rv',markersize=10,label='Dune crest (x={:.2f} m, z={:.2f} m)'.format(x_crest,z_crest))
    plt.plot(x_toe,z_toe,'r^',markersize=10,label='Dune toe (x={:.2f} m, z={:.2f} m)'.format(x_toe,z_toe))
    plt.title('{}: elevations'.format(site))
    plt.legend(loc='best')

    plt.subplot(412)
    d1 = np.diff(zz) / np.diff(xx)
    plt.plot(xx, zz_d1)
    plt.axvline(x_crest,color='red', label='Dune crest')
    plt.axvline(x_toe,color='red', label='Dune toe')
    # plt.ylim([-0.2,0.2])
    plt.title('first derivative - slope')

    plt.subplot(413)
    d2 = np.diff(d1) / np.diff(xx[1:])
    plt.plot(xx, zz_d2)
    plt.axvline(x_crest,color='red', label='Dune crest')
    plt.axvline(x_toe,color='red', label='Dune toe')
    plt.title('second derivative - change in slope')
#     plt.ylim([-0.025,0.025])

    plt.subplot(414)
    plt.plot(xx, zz_d3)
    plt.axvline(x_crest,color='red', label='Dune crest')
    plt.axvline(x_toe,color='red', label='Dune toe')
    plt.title('third derivative')
#     plt.ylim([-0.0025,0.0025])

    plt.tight_layout()
    plt.show()

# xx,zz, x_crest,z_crest, x_toe,z_toe, x_potential_crests,z_potential_crests, x_potential_toes,z_potential_toes = find_crest_and_toes(x,z,x_knots)

# plot_profile(site, x,z, xx,zz, x_crest,z_crest, x_toe,z_toe, x_potential_crests,z_potential_crests, x_potential_toes,z_potential_toes)

In [ ]:
def get_crests_and_toes(site, profile_type, df_profiles):
    x, z = get_profile_data(site, profile_type, df_profiles)
    x_knots, z_knots, best_s = simplify_profile(x, z, site)
    x_knots, z_knots = simplify_segments_with_same_slopes(x_knots, x, z, site, best_s)
#     xs, zs = get_x_z_from_knots(x_knots, z_knots)
    xx,zz, zz_d1,zz_d2,zz_d3,x_crest,z_crest, x_toe,z_toe, x_potential_crests,z_potential_crests, x_potential_toes,z_potential_toes = find_crest_and_toes(x,z,x_knots,best_s)

    plot_profile(site, x,z,  xx,zz, zz_d1,zz_d2,zz_d3,x_crest,z_crest, x_toe,z_toe, x_potential_crests,z_potential_crests, x_potential_toes,z_potential_toes)

    
# site = 'WAMBE0010'
# site = 'NINEMs0048'
# site = 'NAMB0013'
# site = 'AVOCAn0009'
# site = 'GRANTSs0014'
site = 'NARRA0001'

import random
site = random.sample(df_profiles.index.get_level_values('site_id').unique().tolist(), 1)[0]

print(site)
# site='NSHORE_s0014'
get_crests_and_toes(site,'prestorm', df_profiles)

In [ ]:
# Find berms 
for x_knot1, x_knot2, in zip(x_knots[0:-2], x_knots[1:-1]):
    
    # Berms are only located seaward of the dune toe (but sometimes dune toe is undefined, so use dune crest)
    if x_knot1 < x_crest:
        continue
    
    # Get slope of segment
    x_seg, z_seg = xz(x_knot1, x_knot2, x, z)
    slope = get_slope(x_seg, z_seg)
    z_mean = np.mean(z_seg)
    width = x_knot2 - x_knot1
    
    if slope > -0.01:
        print('{:.1f}m wide berm at x={:.1f}m to x={:.1f}m at z={:.1f}m'.format(width, x_knot1, x_knot2, z_mean))

    

In [ ]:
# def reject_outliers(data, m = 5):
#     d = np.abs(data - np.median(data))
#     mdev = np.median(d)
#     s = d/mdev if mdev else 0.
#     return ma.masked_where(s > m, data)

# def hampel(vals_orig, k=7, t0=3):
#     '''
#     vals: pandas series of values from which to remove outliers
#     k: size of window (including the sample; 7 is equal to 3 on either side of value)
#     '''
#     #Make copy so original not edited
#     vals_orig = pd.Series(vals_orig)
#     vals=vals_orig.copy()    
#     #Hampel Filter
#     L= 1.4826
#     rolling_median=vals.rolling(k).median()
#     difference=np.abs(rolling_median-vals)
#     median_abs_deviation=difference.rolling(k).median()
#     threshold= t0 *L * median_abs_deviation
#     outlier_idx=difference>threshold
#     vals[outlier_idx]=np.nan
#     return(vals.tolist())

# # Remove segements where slopes are too high, indicative of a structure
# segments = [xz(x1, x2,x,z) for (x1, x2) in pairwise(x_knots_simplified)]
# slopes = np.array([get_slope(x1,x2) for x1,x2 in segments])
# mask = reject_outliers(np.array(slopes))
# x_knots_filtered = x_knots_simplified[np.append(True,~mask.mask)]
# z_knots_filtered = [z_val for x_val, z_val in zip(x,z) if x_val in x_knots_filtered]



# # Hampel filter based on z values
# mask = ma.masked_invalid(hampel(z_knots_filtered))
# x_knots_filtered = x_knots_filtered[~mask.mask]
# z_knots_filtered = [z_val for x_val, z_val in zip(x,z) if x_val in x_knots_filtered]



# # plt.figure(figsize=(10,5))
# # plt.plot(x_knots_simplified, np.append(slopes[0],slopes), '.-')
# # plt.plot(x_knots_simplified[np.append(True,~mask.mask)], np.append(slopes[~mask.mask][0], slopes[~mask.mask]), '.-')
# # # plt.plot(xs, zs)
# # # plt.plot(x_knots_filtered, z_knots_filtered,'.',markersize=15)
# # plt.show()




# plt.figure(figsize=(10,5))
# plt.plot(x, z, '.-')
# plt.plot(xs, zs)
# plt.plot(x_knots_filtered, z_knots_filtered,'.',markersize=15)
# plt.show()
# z_knots_filtered

## Find dune crests

In [ ]:
from scipy.signal import find_peaks


def crest_by_deriv_2(z):
    """
    Try get crest elevation by taking the difference in 2nd derivative of elevation.
    """

    z = savgol_filter(z, 15, 3, mode='nearest')
    deriv_2_diff = np.diff(np.gradient(z)) * -1

    # Ensure same size arrays for plotting
    deriv_2_diff = np.insert(deriv_2_diff, 0, deriv_2_diff[0])
    med = np.median(deriv_2_diff)
    std = np.std(deriv_2_diff)
    peaks, peak_props = find_peaks(deriv_2_diff, height=med+std*2, distance=10)
    return peaks, peak_props, deriv_2_diff


def crest_by_elevation_peaks(z, min_dune_prominence=1.0):
    # Try find peaks in elevation
    peaks, peak_props = find_peaks(z, distance=10, prominence=min_dune_prominence)
    return peaks, peak_props


def get_dune_crest(x, z, xs,zs, x_knots, z_knots, site):
   
    peaks, peak_props = crest_by_elevation_peaks(z)
    
    if peaks.size != 0:
        # Choose crest by most landward peak
        x_crest = x[peaks[-1]]
        z_crest = z[peaks[-1]]
    
    # If no peaks in elevation are found, find by maximum second derivative
    else:
        peaks, peak_props, deriv_2_diff = crest_by_deriv_2(z)
        
        plt.title(
            '{}: Difference of 2nd derivative in elevation'.format(site))
        plt.xlabel('Distance (m)')
        plt.ylabel('Diff(2nd Derivative Elevation)')
        plt.plot(x, deriv_2_diff)

               
        if peaks.size!= 0:

            # Choose crest by highest peak in diff of 2nd derivative
            i_best = np.argmax(peak_props['peak_heights'])
            x_crest = x[peaks[i_best]]
            z_crest = z[peaks[i_best]]
            plt.plot(
                x[peaks],
                deriv_2_diff[peaks],
                'o',
                markersize=20,
                fillstyle='none')
            plt.show() 
            
        else:
            plt.show() 
            # If no peaks in diff of 2nd derivative are found, take landward most point
            if peaks.size == 0:
                x_crest = x_knots[0]
                z_crest = z_knots[0]

    # Move crest to closest knot
    idx_crest = min(range(len(x_knots)), key=lambda i: abs(x_knots[i]-x_crest))
    x_crest = x_knots[idx_crest]
    z_crest = z_knots[idx_crest]
    
    # Plot for checking
    plt.title('{}: Find dune crest by peak in diff 2nd deriv'.format(site))
    plt.xlabel('Distance (m)')
    plt.ylabel('Elevation (m AHD)')
    plt.plot(x, z, 'k.-', label='Raw profile')
    plt.plot(
        xs,
        zs,
        'r-',
        label='Interpolated profile (s={:.2f})'.format(best_s))
    plt.plot(
        x_knots,
        z_knots,
        'ro',
        markersize=8,
        markeredgewidth=1.5,
        markeredgecolor='orange',
        label='Interpolated knots (n={})'.format(len(x_knots)))
    plt.plot(
        x_crest,
        z_crest,
        'bv',
        markersize=10,
        label='Dune crest (selected) (x={:.1f}m,z={:.1f}m)'.format(x_crest,z_crest))
    plt.plot(
        x[peaks],
        z[peaks],
        'o',
        markersize=10,
        fillstyle='none',
        label='Dune crest (potential)')

    plt.legend(loc='best')
    plt.show()
        
    return x_crest, z_crest
        
x_crest, z_crest = get_dune_crest(x, z, xs,zs, x_knots, z_knots, site)

In [ ]:
# Get toe by second derivative
def toe_by_deriv_2(z):
    """
    Try get crest elevation by taking the difference in 2nd derivative of elevation.
    """

    z = savgol_filter(z,11, 3, mode='nearest')
    deriv_2_diff = np.diff(np.gradient(z))

    # Ensure same size arrays for plotting
    deriv_2_diff = np.insert(deriv_2_diff, 0, deriv_2_diff[0])
    med = np.median(deriv_2_diff)
    std = np.std(deriv_2_diff)
    peaks, peak_props = find_peaks(deriv_2_diff, height=max(0.01,med+std*3), distance=10)
    return peaks, peak_props, deriv_2_diff

def get_dune_toe(x, z, xs,zs, x_crest,z_crest,x_knots, z_knots, site):
    peaks, peak_props, deriv_2_diff = toe_by_deriv_2(z)

    plt.title('{}: Difference of 2nd derivative in elevation'.format(site))
    plt.xlabel('Distance (m)')
    plt.ylabel('Diff(2nd Derivative Elevation)')
    plt.plot(x, deriv_2_diff)
    
    if peaks.size!= 0:
        
        # Remove peaks which are behind the crest
        # TODO What happens if all peaks are removed?
        mask = ma.masked_where(x[peaks] <= x_crest, x[peaks])
        peaks = peaks[~mask.mask]

    if peaks.size!= 0:
        # Choose toe by highest peak in diff of 2nd derivative
        i_best = np.argmax(peak_props['peak_heights'])
        x_toe = x[peaks[i_best]][0]
        z_toe = z[peaks[i_best]][0]
#         # Move crest to closest knot
#         idx_toe = min(range(len(x_knots)), key=lambda i: abs(x_knots[i]-x_toe))
#         x_toe = x_knots[idx_toe]
#         z_toe = z_knots[idx_toe]

        plt.plot(
            x[peaks],
            deriv_2_diff[peaks],
            'o',
            markersize=20,
            fillstyle='none')
        plt.show()
    else:
        x_toe = np.nan
        z_toe = np.nan
        plt.show()

    # Plot for checking
    plt.title('{}: Find dune crest by peak in diff 2nd deriv'.format(site))
    plt.xlabel('Distance (m)')
    plt.ylabel('Elevation (m AHD)')
    plt.plot(x, z, 'k.-', label='Raw profile')
    plt.plot(
        xs,
        zs,
        'r-',
        label='Interpolated profile (s={:.2f})'.format(best_s))
    plt.plot(
        x_knots,
        z_knots,
        'ro',
        markersize=8,
        markeredgewidth=1.5,
        markeredgecolor='orange',
        label='Interpolated knots (n={})'.format(len(x_knots)))
    plt.plot(
        x_crest,
        z_crest,
        'bv',
        markersize=10,
        label='Dune crest(x={:.1f} m,z={:.1f} m)'.format(x_crest,z_crest))
    plt.plot(
        x_toe,
        z_toe,
        'b^',
        markersize=10,
        label='Dune toe (x={:.1f} m,z={:.1f} m)'.format(x_toe,z_toe))

    plt.legend(loc='best')
    plt.show()
    return x_toe, z_toe
x_toe, z_toe = get_dune_toe(x, z, xs,zs, x_crest,z_crest,x_knots, z_knots, site)

In [ ]:
def find_dune_crest_and_toe(site, profile_type, df_profiles):
    x, z = get_profile_data(site, profile_type, df_profiles)
    x_knots, z_knots = simplify_profile(x, z, site)
    x_knots, z_knots = simplify_segments_with_same_slopes(x_knots, x, z, site)
    xs, zs = get_x_z_from_knots(x_knots, z_knots)
    x_crest, z_crest = get_dune_crest(x, z, xs,zs, x_knots, z_knots, site)
    x_toe, z_toe = get_dune_toe(x, z, xs,zs, x_crest,z_crest,x_knots, z_knots, site)
    
find_dune_crest_and_toe('ENTRA0004', 'prestorm', df_profiles)
